In [526]:
import json
from collections import defaultdict
import pandas as pd

In [3]:
with open("message_imatinib_asthma_output3.json","r") as inf:
    response = json.load(inf)

In [4]:
results = response["message"]["results"]

In [5]:
len(results)

567

In [8]:
print(json.dumps(response["message"]["query_graph"], indent=2))

{
  "nodes": {
    "n0": {
      "ids": [
        "PUBCHEM.COMPOUND:5291"
      ],
      "name": "imatinib"
    },
    "n1": {
      "ids": [
        "MONDO:0004979"
      ],
      "name": "asthma"
    },
    "un": {
      "categories": [
        "biolink:NamedThing"
      ]
    }
  },
  "edges": {
    "e0": {
      "subject": "n0",
      "object": "n1",
      "predicates": [
        "biolink:related_to"
      ]
    },
    "e1": {
      "subject": "n0",
      "object": "un",
      "predicates": [
        "biolink:related_to"
      ]
    },
    "e2": {
      "subject": "n1",
      "object": "un",
      "predicates": [
        "biolink:related_to"
      ]
    }
  }
}


In [9]:
results[0]

{'node_bindings': {'n0': [{'id': 'CHEBI:45783', 'attributes': []}],
  'un': [{'id': 'PUBCHEM.COMPOUND:123596', 'attributes': []}],
  'n1': [{'id': 'MONDO:0004979', 'attributes': []}]},
 'analyses': [{'resource_id': 'infores:aragorn',
   'edge_bindings': {'e0': [{'id': '6323dbd0243511efbba01a583b18729b',
      'attributes': []}],
    'e1': [{'id': '6323dd38243511efbba01a583b18729b', 'attributes': []}],
    'e2': [{'id': '6323dd4c243511efbba01a583b18729b', 'attributes': []}]}}]}

In [10]:
response["message"]["knowledge_graph"]["edges"]["6323dbd0243511efbba01a583b18729b"]

{'subject': 'CHEBI:45783',
 'object': 'MONDO:0004979',
 'predicate': 'biolink:related_to',
 'sources': [{'resource_id': 'infores:shadowfax',
   'resource_role': 'primary_knowledge_source'}],
 'attributes': [{'attribute_type_id': 'biolink:support_graphs',
   'value': ['...',
    ...]}]}

In [12]:
len(response["message"]["knowledge_graph"]["edges"]["6323dbd0243511efbba01a583b18729b"]["attributes"][0]["value"])

1016

In [648]:
def choose_edge(predicates):
    order = { "biolink:related_to": 1,
             "biolink:occurs_together_in_literature_with": 1,
             "biolink:overlaps": 3,
             "biolink:coexists_with": 3,
             "biolink:has_part": 4,
             "biolink:located_in": 4,
             "biolink:expresses": 3, 
             "biolink:expressed_in": 3, #one of these is noncanonical
             "biolink:disease_has_location": 5,
            "biolink:subclass_of": 2,
            "biolink:treats_or_applied_or_studied_to_treat": 3,
             "biolink:in_clinical_trials_for": 3,
             "biolink:prevents": 4,
             "biolink:treats": 4,
             "biolink:ameliorates_condition": 4,
             "biolink:has_adverse_event": 4,
             "biolink:has_side_effect": 4,
             "biolink:contraindicated_in": 4,
             "biolink:contraindicated_for": 4, #does this exist?
            "biolink:associated_with": 2,
            "biolink:correlated_with": 2,
             "biolink:similar_to": 3,
             "biolink:affects": 3,
             "biolink:positively_correlated_with": 3,
             "biolink:negatively_correlated_with": 3,
            "biolink:genetically_associated_with": 3,
             "biolink:gene_associated_with_condition": 3,
            "biolink:contributes_to": 4,
             "biolink:manifestation_of":4,
             "biolink:biomarker_for": 4,
             "biolink:has_phenotype": 4,
             "biolink:diagnoses":4, 
             "biolink:predisposes": 4,
             "biolink:interacts_with": 3,
             "biolink:physically_interacts_with": 4,
             "biolink:directly_physically_interacts_with": 5,
             "biolink:causes": 5,
             "biolink:disrupts": 5,
            "biolink:catalyzes": 4,
            "biolink:participates_in": 4,
            "biolink:has_participant": 4, # one of these is non canonical
             "biolink:enables": 4,
            "biolink:decreases_response_to": 5,
             "biolink:increases_response_to": 5,
             "biolink:target_for": 5,
             "biolink:affects.abundance": 4, # no direction
            'biolink:affects.increased.activity_or_abundance': 6,
            'biolink:affects.decreased.activity_or_abundance': 6,
            "biolink:regulates.upregulated": 6,
            "biolink:regulates.downregulated": 6,
            "decreased.susceptibility.biolink:affected_by": 6,
            "biolink:affects.decreased.activity": 6,
            "biolink:affects.increased.activity": 6,
            "biolink:affects.decreased.expression": 6,
            "biolink:binds": 6,
            "compound_treatment.biolink:correlated_with.gene_knockdown": 5, #who is doing this mess?
            }
    inverted={f"Inverse({k})": v for k,v in order.items()}
    order.update(inverted)
    ranked = [ (order[p], p) for p in predicates ]
    ranked.sort()
    ranked.reverse()
    best_score = max( x[0] for x in ranked )
    best_preds =  list(set([ x[1] for x in ranked if x[0] == best_score ]))
    if len(best_preds) == 1:
        return best_preds[0]
    return f"({','.join(best_preds)})"

def get_cat(cat_list):
    good_ones = ["biolink:Disease", "biolink:PhenotypicFeature", "biolink:Gene", "biolink:MolecularActivity", 
                 "biolink:ChemicalEntity", "biolink:AnatomicalEntity", "biolink:BiologicalProcessOrActivity"]
    for go in good_ones:
        if go in cat_list:
            return go
    print(cat_list)
    fuckyoufucker

In [619]:
def find_qualifier(edge, qualname):
    qualifiers = edge["qualifiers"]
    for q in qualifiers:
        if q["qualifier_type_id"] == qualname:
            return q["qualifier_value"]
    return None
    
def rewrite_edge(edge):
    #Assume that we are dealing only with object qualifiers for now
    subject_aspect_qualifier = find_qualifier(edge, "biolink:subject_aspect_qualifier")
    subject_direction_qualifier = find_qualifier(edge, "biolink:subject_direction_qualifier")
    object_aspect_qualifier = find_qualifier(edge, "biolink:object_aspect_qualifier")
    object_direction_qualifier = find_qualifier(edge, "biolink:object_direction_qualifier")
    newpred = [subject_direction_qualifier, subject_aspect_qualifier, edge["predicate"], object_direction_qualifier, object_aspect_qualifier]
    newpred = [x for x in newpred if x is not None]
    #if len(newpred) == 1:
    #    print(json.dumps(edge,indent=2))
    #    blart
    newpredicate = '.'.join(newpred)
    #if newpredicate == "biolink:affects.decreased.activity":
    #    print(json.dumps(edge,indent=2))
    #    print('+++++++++++++++++++++++++++++++++++++++++++++++++++++')
    edge["predicate"] = newpredicate
    edge["qualifiers"] = None

def invert(predicate):
    #symmetry!
    if predicate in ["biolink:related_to", "biolink:associated_with", "biolink:correlated_with"]:
        return predicate
    return f"Inverse({predicate})"

In [642]:
def parse_path(support_graph_id, response, n0, n1):
    message = response["message"]
    aux_graphs = message["auxiliary_graphs"]
    kgraph = message["knowledge_graph"]
    edges = kgraph["edges"]
    nodes = kgraph["nodes"]
    path_edges = aux_graphs[support_graph_id]["edges"]
    predicates = defaultdict(list)
    names = {}
    categories={}
    for path_edge in path_edges:
        edge=edges[path_edge]
        if edge["qualifiers"]:
            rewrite_edge(edge)
        subject = edge["subject"]
        object = edge["object"]
        predicate = edge["predicate"]
        if (object,subject) in predicates:
            #Ths is nasty 
            predicates[(object,subject)].append( invert(predicate) )
        else:
            predicates[ (subject,object) ].append(predicate)
        names[subject] = nodes[subject]["name"]
        names[object] = nodes[object]["name"]
        #why aren't these categories sorted?  Where is this fucking ordering coming from?
        categories[subject] = get_cat(nodes[subject]["categories"])
        categories[object] = get_cat(nodes[object]["categories"])
    if len(predicates) > 4:
        for (s,o),plist in predicates.items():
            bpred=choose_edge(plist)
            print( names[s], bpred, names[o] )
        bleah
    path = [n0]
    for (s,o),plist in predicates.items():
        bpred=choose_edge(plist)
        if s == path[-1]:
            path.append( bpred )
            path.append( o )
        else:
            path.append( f"Inverse({bpred})")
            path.append(s)
        #print( names[s], bpred, names[o] )
    assert(path[-1] == n1)
    namepath = [ names[p] if i % 2 == 0 else p for i,p in enumerate(path) ]
    mpl = []
    for i in range(0, len(path)-1, 2):
        mpl.append( categories[path[i]] )
        mpl.append( path[i+1] )
    mpl.append( categories[path[-1]] )
    metapath = tuple(mpl)
    return metapath, namepath
        

In [643]:
def get_supports(path_edge):
    for att in path_edge["attributes"]:
        if att["attribute_type_id"] == "biolink:support_graphs":
            return att["value"]
    return None

def write_result_paths(response,result_number):
    results = response["message"]["results"]
    result = results[result_number]
    n0 = result["node_bindings"]["n0"][0]["id"]
    n1 = result["node_bindings"]["n1"][0]["id"]
    k_node_id = result["node_bindings"]["un"][0]["id"]
    print(response["message"]["knowledge_graph"]["nodes"][k_node_id]["name"])
    k_edge_id = result["analyses"][0]["edge_bindings"]["e0"][0]["id"]
    path_edge = response["message"]["knowledge_graph"]["edges"][k_edge_id]
    supports = get_supports(path_edge)
    print(len(supports),"paths")
    
    meta2paths = defaultdict(list)
    for support in supports:
        metapath,path = parse_path(support, response, n0, n1)
        meta2paths[metapath].append(path)
    best_mets = [(len(meta2paths[metapath]),metapath) for metapath in meta2paths]
    best_mets.sort()
    best_mets.reverse()
    print (len(meta2paths), "metapaths")
    print("-=-=-=-=-=-=-=-=-=-=")
    mpc = 1
    for c,metapath in best_mets:
        table = pd.DataFrame( columns = metapath )
        nodecounts = [ defaultdict(int) for p in metapath ]
        np = 0
        for path in meta2paths[metapath]:
            np += 1
            for k, c in zip(path, nodecounts):
                c[k] += 1
        row = []
        for counter in nodecounts:
            wrote = False
            for n,c in counter.items():
                f = c / np
                if f > 0.5:
                    if wrote== True:
                        print(counter)
                        print(np)
                        shit
                    row.append( f"{n} ({f})" )
                    wrote = True
            if not wrote:
                row.append(len(counter))
        table.loc[1] = row
        for i,path in enumerate(meta2paths[metapath]):
            table.loc[i+2] = path
        pd.set_option('display.max_rows', None)
        print(mpc)
        mpc += 1
        display(table)

In [644]:
#not optimized for actual bulk use, just a quick lookup
def find_edges(response, subject_name, object_name, predicate):
    message = response["message"]
    kg = message["knowledge_graph"]
    nodes = kg["nodes"]
    edges = kg["edges"]
    subject = None
    object = None
    for node_id, node in nodes.items():
        if node["name"] == subject_name:
            subject = node_id
        if node["name"] == object_name:
            object = node_id
        if subject and object:
            break
    for edge_id, edge in edges.items():
        if edge["subject"] == subject and edge["object"] == object and edge["predicate"] == predicate:
            print(json.dumps(edge,indent=2))
            print('-------')

In [645]:
write_result_paths(response,0)

IMATINIB MESYLATE
1016 paths
324 metapaths
-=-=-=-=-=-=-=-=-=-=
1


biolink:ChemicalEntity        Inverse(biolink:has_part)  \
1          imatinib (1.0)  Inverse(biolink:has_part) (1.0)   
2                imatinib        Inverse(biolink:has_part)   
3                imatinib        Inverse(biolink:has_part)   
4                imatinib        Inverse(biolink:has_part)   
5                imatinib        Inverse(biolink:has_part)   
6                imatinib        Inverse(biolink:has_part)   
7                imatinib        Inverse(biolink:has_part)   
8                imatinib        Inverse(biolink:has_part)   
9                imatinib        Inverse(biolink:has_part)   
10               imatinib        Inverse(biolink:has_part)   
11               imatinib        Inverse(biolink:has_part)   
12               imatinib        Inverse(biolink:has_part)   
13               imatinib        Inverse(biolink:has_part)   
14               imatinib        Inverse(biolink:has_part)   
15               imatinib        Inverse(biolink:has_part)   
16               imatinib        Inverse(biolink:has_part)   
17               imatinib        Inverse(biolink:has_part)   
18               imatinib        Inverse(biolink:has_part)   
19               imatinib        Inverse(biolink:has_part)   
20               imatinib        Inverse(biolink:has_part)   
21               imatinib        Inverse(biolink:has_part)   
22               imatinib        Inverse(biolink:has_part)   
23               imatinib        Inverse(biolink:has_part)   
24               imatinib        Inverse(biolink:has_part)   
25               imatinib        Inverse(biolink:has_part)   
26               imatinib        Inverse(biolink:has_part)   
27               imatinib        Inverse(biolink:has_part)   
28               imatinib        Inverse(biolink:has_part)   
29               imatinib        Inverse(biolink:has_part)   
30               imatinib        Inverse(biolink:has_part)   
31               imatinib        Inverse(biolink:has_part)   
32               imatinib        Inverse(biolink:has_part)   
33               imatinib        Inverse(biolink:has_part)   
34               imatinib        Inverse(biolink:has_part)   
35               imatinib        Inverse(biolink:has_part)   
36               imatinib        Inverse(biolink:has_part)   
37               imatinib        Inverse(biolink:has_part)   
38               imatinib        Inverse(biolink:has_part)   
39               imatinib        Inverse(biolink:has_part)   
40               imatinib        Inverse(biolink:has_part)   
41               imatinib        Inverse(biolink:has_part)   
42               imatinib        Inverse(biolink:has_part)   
43               imatinib        Inverse(biolink:has_part)   
44               imatinib        Inverse(biolink:has_part)   
45               imatinib        Inverse(biolink:has_part)   
46               imatinib        Inverse(biolink:has_part)   
47               imatinib        Inverse(biolink:has_part)   
48               imatinib        Inverse(biolink:has_part)   
49               imatinib        Inverse(biolink:has_part)   
50               imatinib        Inverse(biolink:has_part)   
51               imatinib        Inverse(biolink:has_part)   
52               imatinib        Inverse(biolink:has_part)   
53               imatinib        Inverse(biolink:has_part)   
54               imatinib        Inverse(biolink:has_part)   
55               imatinib        Inverse(biolink:has_part)   
56               imatinib        Inverse(biolink:has_part)   
57               imatinib        Inverse(biolink:has_part)   
58               imatinib        Inverse(biolink:has_part)   
59               imatinib        Inverse(biolink:has_part)   
60               imatinib        Inverse(biolink:has_part)   
61               imatinib        Inverse(biolink:has_part)   
62               imatinib        Inverse(biolink:has_part)   
63               imatinib        Inverse(biolink:has_part)   
64               imatinib        In

2


biolink:ChemicalEntity        Inverse(biolink:has_part)  \
1          imatinib (1.0)  Inverse(biolink:has_part) (1.0)   
2                imatinib        Inverse(biolink:has_part)   
3                imatinib        Inverse(biolink:has_part)   
4                imatinib        Inverse(biolink:has_part)   
5                imatinib        Inverse(biolink:has_part)   
6                imatinib        Inverse(biolink:has_part)   
7                imatinib        Inverse(biolink:has_part)   
8                imatinib        Inverse(biolink:has_part)   
9                imatinib        Inverse(biolink:has_part)   
10               imatinib        Inverse(biolink:has_part)   
11               imatinib        Inverse(biolink:has_part)   
12               imatinib        Inverse(biolink:has_part)   
13               imatinib        Inverse(biolink:has_part)   
14               imatinib        Inverse(biolink:has_part)   
15               imatinib        Inverse(biolink:has_part)   
16               imatinib        Inverse(biolink:has_part)   
17               imatinib        Inverse(biolink:has_part)   
18               imatinib        Inverse(biolink:has_part)   
19               imatinib        Inverse(biolink:has_part)   
20               imatinib        Inverse(biolink:has_part)   
21               imatinib        Inverse(biolink:has_part)   
22               imatinib        Inverse(biolink:has_part)   
23               imatinib        Inverse(biolink:has_part)   
24               imatinib        Inverse(biolink:has_part)   
25               imatinib        Inverse(biolink:has_part)   
26               imatinib        Inverse(biolink:has_part)   
27               imatinib        Inverse(biolink:has_part)   
28               imatinib        Inverse(biolink:has_part)   
29               imatinib        Inverse(biolink:has_part)   
30               imatinib        Inverse(biolink:has_part)   
31               imatinib        Inverse(biolink:has_part)   
32               imatinib        Inverse(biolink:has_part)   
33               imatinib        Inverse(biolink:has_part)   
34               imatinib        Inverse(biolink:has_part)   
35               imatinib        Inverse(biolink:has_part)   
36               imatinib        Inverse(biolink:has_part)   
37               imatinib        Inverse(biolink:has_part)   
38               imatinib        Inverse(biolink:has_part)   
39               imatinib        Inverse(biolink:has_part)   

     biolink:ChemicalEntity        biolink:associated_with  \
1   IMATINIB MESYLATE (1.0)  biolink:associated_with (1.0)   
2         IMATINIB MESYLATE        biolink:associated_with   
3         IMATINIB MESYLATE        biolink:associated_with   
4         IMATINIB MESYLATE        biolink:associated_with   
5         IMATINIB MESYLATE        biolink:associated_with   
6         IMATINIB MESYLATE        biolink:associated_with   
7         IMATINIB MESYLATE        biolink:associated_with   
8         IMATINIB MESYLATE        biolink:associated_with   
9         IMATINIB MESYLATE        biolink:associated_with   
10        IMATINIB MESYLATE        biolink:associated_with   
11        IMATINIB MESYLATE        biolink:associated_with   
12        IMATINIB MESYLATE        biolink:associated_with   
13        IMATINIB MESYLATE        biolink:associated_with   
14        IMATINIB MESYLATE        biolink:associated_with   
15        IMATINIB MESYLATE        biolink:associated_with   
16        IMATINIB MESYLATE        biolink:associated_with   
17        IMATINIB MESYLATE        biolink:associated_with   
18        IMATINIB MESYLATE        biolink:associated_with   
19        IMATINIB MESYLATE        biolink:associated_with   
20        IMATINIB MESYLATE        biolink:associated_with   
21        IMATINIB MESYLATE        biolink:associated_with   
22        IMATINIB MESYLATE        biolink:associated_with   
23        IMATINIB MESYLATE        biolink:associated_with   
24        IMATINIB MESYLATE       

3


...

biolink:ChemicalEntity  \
1         imatinib (1.0)   
2               imatinib   

  (biolink:binds,biolink:affects.decreased.activity_or_abundance,biolink:affects.decreased.expression,biolink:affects.decreased.activity,biolink:affects.increased.activity)  \
1  (biolink:binds,biolink:affects.decreased.activ...                                                                                                                           
2  (biolink:binds,biolink:affects.decreased.activ...                                                                                                                           

   biolink:Gene  \
1  PDGFRA (1.0)   
2        PDGFRA   

  Inverse((biolink:affects.decreased.expression,biolink:affects.decreased.activity))  \
1  Inverse((biolink:affects.decreased.expression,...                                   
2  Inverse((biolink:affects.decreased.expression,...                                   

    biolink:ChemicalEntity        biolink:affects biolink:Gene  \
1  IMATINIB MESYLATE (1.0)  biolink:affects (1.0)   CCL2 (1.0)   
2        IMATINIB MESYLATE        biolink:affects         CCL2   

  Inverse(Inverse(biolink:genetically_associated_with)) biolink:Disease  
1  Inverse(Inverse(biolink:genetically_associated...       asthma (1.0)  
2  Inverse(Inverse(biolink:genetically_associated...             asthma

323


biolink:ChemicalEntity  \
1         imatinib (1.0)   
2               imatinib   

  (biolink:affects.increased.activity,biolink:affects.decreased.activity,biolink:binds,biolink:affects.decreased.activity_or_abundance)  \
1  (biolink:affects.increased.activity,biolink:af...                                                                                      
2  (biolink:affects.increased.activity,biolink:af...                                                                                      

  biolink:Gene  \
1    KIT (1.0)   
2          KIT   

  Inverse((biolink:affects.increased.activity,biolink:affects.decreased.activity))  \
1  Inverse((biolink:affects.increased.activity,bi...                                 
2  Inverse((biolink:affects.increased.activity,bi...                                 

    biolink:ChemicalEntity        biolink:affects biolink:Gene  \
1  IMATINIB MESYLATE (1.0)  biolink:affects (1.0)   CCL2 (1.0)   
2        IMATINIB MESYLATE        biolink:affects         CCL2   

  Inverse(Inverse(biolink:genetically_associated_with)) biolink:Disease  
1  Inverse(Inverse(biolink:genetically_associated...       asthma (1.0)  
2  Inverse(Inverse(biolink:genetically_associated...             asthma

324


biolink:ChemicalEntity  \
1         imatinib (1.0)   
2               imatinib   

  (biolink:affects.decreased.activity,biolink:binds,biolink:affects.increased.activity_or_abundance)  \
1  (biolink:affects.decreased.activity,biolink:bi...                                                   
2  (biolink:affects.decreased.activity,biolink:bi...                                                   

  biolink:Gene Inverse(decreased.susceptibility.biolink:affected_by)  \
1    LYN (1.0)  Inverse(decreased.susceptibility.biolink:affec...      
2          LYN  Inverse(decreased.susceptibility.biolink:affec...      

    biolink:ChemicalEntity        biolink:affects biolink:Gene  \
1  IMATINIB MESYLATE (1.0)  biolink:affects (1.0)   CCL2 (1.0)   
2        IMATINIB MESYLATE        biolink:affects         CCL2   

  Inverse(Inverse(biolink:genetically_associated_with)) biolink:Disease  
1  Inverse(Inverse(biolink:genetically_associated...       asthma (1.0)  
2  Inverse(Inverse(biolink:genetically_associated...             asthma

In [649]:
write_result_paths(response,2)

nilotinib
2570 paths
669 metapaths
-=-=-=-=-=-=-=-=-=-=
1


biolink:ChemicalEntity        biolink:similar_to biolink:ChemicalEntity  \
1           imatinib (1.0)  biolink:similar_to (1.0)        nilotinib (1.0)   
2                 imatinib        biolink:similar_to              nilotinib   
3                 imatinib        biolink:similar_to              nilotinib   
4                 imatinib        biolink:similar_to              nilotinib   
5                 imatinib        biolink:similar_to              nilotinib   
6                 imatinib        biolink:similar_to              nilotinib   
7                 imatinib        biolink:similar_to              nilotinib   
8                 imatinib        biolink:similar_to              nilotinib   
9                 imatinib        biolink:similar_to              nilotinib   
10                imatinib        biolink:similar_to              nilotinib   
11                imatinib        biolink:similar_to              nilotinib   
12                imatinib        biolink:similar_to              nilotinib   
13                imatinib        biolink:similar_to              nilotinib   
14                imatinib        biolink:similar_to              nilotinib   
15                imatinib        biolink:similar_to              nilotinib   
16                imatinib        biolink:similar_to              nilotinib   
17                imatinib        biolink:similar_to              nilotinib   
18                imatinib        biolink:similar_to              nilotinib   
19                imatinib        biolink:similar_to              nilotinib   
20                imatinib        biolink:similar_to              nilotinib   
21                imatinib        biolink:similar_to              nilotinib   
22                imatinib        biolink:similar_to              nilotinib   
23                imatinib        biolink:similar_to              nilotinib   
24                imatinib        biolink:similar_to              nilotinib   
25                imatinib        biolink:similar_to              nilotinib   
26                imatinib        biolink:similar_to              nilotinib   
27                imatinib        biolink:similar_to              nilotinib   
28                imatinib        biolink:similar_to              nilotinib   
29                imatinib        biolink:similar_to              nilotinib   
30                imatinib        biolink:similar_to              nilotinib   
31                imatinib        biolink:similar_to              nilotinib   
32                imatinib        biolink:similar_to              nilotinib   
33                imatinib        biolink:similar_to              nilotinib   
34                imatinib        biolink:similar_to              nilotinib   
35                imatinib        biolink:similar_to              nilotinib   
36                imatinib        biolink:similar_to              nilotinib   
37                imatinib        biolink:similar_to              nilotinib   
38                imatinib        biolink:similar_to              nilotinib   
39                imatinib        biolink:similar_to              nilotinib   
40                imatinib        biolink:similar_to              nilotinib   
41                imatinib        biolink:similar_to              nilotinib   
42                imatinib        biolink:similar_to              nilotinib   
43                imatinib        biolink:similar_to              nilotinib   
44                imatinib        biolink:similar_to              nilotinib   
45                imatinib        biolink:similar_to              nilotinib   
46                imatinib        biolink:similar_to              nilotinib   
47                imatinib        biolink:similar_to              nilotinib   
48                imatinib        biolink:similar_to              nilotinib   
49                imatinib        biolink:similar_to              nilotinib   
50                imatinib        biolink:similar_to  

2


biolink:ChemicalEntity        biolink:similar_to biolink:ChemicalEntity  \
1           imatinib (1.0)  biolink:similar_to (1.0)        nilotinib (1.0)   
2                 imatinib        biolink:similar_to              nilotinib   
3                 imatinib        biolink:similar_to              nilotinib   
4                 imatinib        biolink:similar_to              nilotinib   
5                 imatinib        biolink:similar_to              nilotinib   
6                 imatinib        biolink:similar_to              nilotinib   
7                 imatinib        biolink:similar_to              nilotinib   
8                 imatinib        biolink:similar_to              nilotinib   
9                 imatinib        biolink:similar_to              nilotinib   
10                imatinib        biolink:similar_to              nilotinib   
11                imatinib        biolink:similar_to              nilotinib   
12                imatinib        biolink:similar_to              nilotinib   
13                imatinib        biolink:similar_to              nilotinib   
14                imatinib        biolink:similar_to              nilotinib   
15                imatinib        biolink:similar_to              nilotinib   
16                imatinib        biolink:similar_to              nilotinib   
17                imatinib        biolink:similar_to              nilotinib   
18                imatinib        biolink:similar_to              nilotinib   
19                imatinib        biolink:similar_to              nilotinib   
20                imatinib        biolink:similar_to              nilotinib   
21                imatinib        biolink:similar_to              nilotinib   
22                imatinib        biolink:similar_to              nilotinib   
23                imatinib        biolink:similar_to              nilotinib   
24                imatinib        biolink:similar_to              nilotinib   
25                imatinib        biolink:similar_to              nilotinib   
26                imatinib        biolink:similar_to              nilotinib   
27                imatinib        biolink:similar_to              nilotinib   
28                imatinib        biolink:similar_to              nilotinib   
29                imatinib        biolink:similar_to              nilotinib   
30                imatinib        biolink:similar_to              nilotinib   
31                imatinib        biolink:similar_to              nilotinib   
32                imatinib        biolink:similar_to              nilotinib   
33                imatinib        biolink:similar_to              nilotinib   
34                imatinib        biolink:similar_to              nilotinib   
35                imatinib        biolink:similar_to              nilotinib   
36                imatinib        biolink:similar_to              nilotinib   
37                imatinib        biolink:similar_to              nilotinib   
38                imatinib        biolink:similar_to              nilotinib   
39                imatinib        biolink:similar_to              nilotinib   
40                imatinib        biolink:similar_to              nilotinib   
41                imatinib        biolink:similar_to              nilotinib   
42                imatinib        biolink:similar_to              nilotinib   
43                imatinib        biolink:similar_to              nilotinib   
44                imatinib        biolink:similar_to              nilotinib   
45                imatinib        biolink:similar_to              nilotinib   
46                imatinib        biolink:similar_to              nilotinib   
47                imatinib        biolink:similar_to              nilotinib   
48                imatinib        biolink:similar_to              nilotinib   
49                imatinib        biolink:similar_to              nilotinib   
50                imatinib        biolink:similar_to  

3


...

biolink:ChemicalEntity  \
1         imatinib (1.0)   
2               imatinib   

  (biolink:affects.decreased.activity,biolink:binds,biolink:affects.increased.activity_or_abundance)  \
1  (biolink:affects.decreased.activity,biolink:bi...                                                   
2  (biolink:affects.decreased.activity,biolink:bi...                                                   

  biolink:Gene  \
1    LYN (1.0)   
2          LYN   

  Inverse((biolink:affects.decreased.activity,biolink:binds,biolink:regulates.upregulated))  \
1  Inverse((biolink:affects.decreased.activity,bi...                                          
2  Inverse((biolink:affects.decreased.activity,bi...                                          

  biolink:ChemicalEntity  \
1        nilotinib (1.0)   
2              nilotinib   

  (biolink:affects.decreased.activity_or_abundance,biolink:regulates.upregulated)  \
1  (biolink:affects.decreased.activity_or_abundan...                                
2  (biolink:affects.decreased.activity_or_abundan...                                

  biolink:Gene Inverse(Inverse(biolink:genetically_associated_with))  \
1   CCL2 (1.0)  Inverse(Inverse(biolink:genetically_associated...      
2         CCL2  Inverse(Inverse(biolink:genetically_associated...      

  biolink:Disease  
1    asthma (1.0)  
2          asthma

668


biolink:ChemicalEntity  \
1         imatinib (1.0)   
2               imatinib   

  (biolink:affects.decreased.activity,biolink:binds,biolink:affects.increased.activity_or_abundance)  \
1  (biolink:affects.decreased.activity,biolink:bi...                                                   
2  (biolink:affects.decreased.activity,biolink:bi...                                                   

  biolink:Gene Inverse((biolink:affects.decreased.activity,biolink:binds))  \
1    LYN (1.0)  Inverse((biolink:affects.decreased.activity,bi...            
2          LYN  Inverse((biolink:affects.decreased.activity,bi...            

  biolink:ChemicalEntity        biolink:similar_to biolink:ChemicalEntity  \
1        ponatinib (1.0)  biolink:similar_to (1.0)        nilotinib (1.0)   
2              ponatinib        biolink:similar_to              nilotinib   

       biolink:treats_or_applied_or_studied_to_treat biolink:Disease  
1  biolink:treats_or_applied_or_studied_to_treat ...    asthma (1.0)  
2      biolink:treats_or_applied_or_studied_to_treat          asthma

669


biolink:ChemicalEntity  \
1         imatinib (1.0)   
2               imatinib   

  (biolink:affects.decreased.activity,biolink:binds,biolink:affects.increased.activity_or_abundance)  \
1  (biolink:affects.decreased.activity,biolink:bi...                                                   
2  (biolink:affects.decreased.activity,biolink:bi...                                                   

  biolink:Gene Inverse((biolink:affects.decreased.activity,biolink:binds))  \
1    LYN (1.0)  Inverse((biolink:affects.decreased.activity,bi...            
2          LYN  Inverse((biolink:affects.decreased.activity,bi...            

  biolink:ChemicalEntity  \
1       NINTEDANIB (1.0)   
2             NINTEDANIB   

  (biolink:physically_interacts_with,Inverse(biolink:physically_interacts_with))  \
1  (biolink:physically_interacts_with,Inverse(bio...                               
2  (biolink:physically_interacts_with,Inverse(bio...                               

  biolink:ChemicalEntity      biolink:treats_or_applied_or_studied_to_treat  \
1        nilotinib (1.0)  biolink:treats_or_applied_or_studied_to_treat ...   
2              nilotinib      biolink:treats_or_applied_or_studied_to_treat   

  biolink:Disease  
1    asthma (1.0)  
2          asthma

In [624]:
find_edges(response, "bronchus", "CCL2", "biolink:regulates.upregulated")

{
  "subject": "UBERON:0002185",
  "object": "NCBIGene:6347",
  "predicate": "biolink:regulates.upregulated",
  "sources": [
    {
      "resource_id": "infores:aragorn",
      "resource_role": "aggregator_knowledge_source",
      "upstream_resource_ids": [
        "infores:automat-hetionet"
      ],
      "source_record_urls": null
    },
    {
      "resource_id": "infores:bgee",
      "resource_role": "primary_knowledge_source",
      "upstream_resource_ids": null,
      "source_record_urls": null
    },
    {
      "resource_id": "infores:automat-robokop",
      "resource_role": "aggregator_knowledge_source",
      "upstream_resource_ids": [
        "infores:hetionet"
      ],
      "source_record_urls": null
    },
    {
      "resource_id": "infores:automat-hetionet",
      "resource_role": "aggregator_knowledge_source",
      "upstream_resource_ids": [
        "infores:hetionet"
      ],
      "source_record_urls": null
    },
    {
      "resource_id": "infores:hetionet",
     

In [639]:

for q in range(1,100):
    print(int((q-1) / 2))

0
0
1
1
2
2
3
3
4
4
5
5
6
6
7
7
8
8
9
9
10
10
11
11
12
12
13
13
14
14
15
15
16
16
17
17
18
18
19
19
20
20
21
21
22
22
23
23
24
24
25
25
26
26
27
27
28
28
29
29
30
30
31
31
32
32
33
33
34
34
35
35
36
36
37
37
38
38
39
39
40
40
41
41
42
42
43
43
44
44
45
45
46
46
47
47
48
48
49
